In [1]:
import matplotlib.pyplot as plt
%matplotlib inline

import os

import pandas as pd
import numpy as np


from funcs.helper import read_custom_aperture_lc, fetch_lightcurve
from funcs.multiperiod import show_flare, find_period

import time as Timestamp
from scipy import optimize

tstamp = Timestamp.strftime("%d_%m_%Y", Timestamp.localtime())

import emcee
import corner

/home/ekaterina/Documents/000_envs/forallpurposes/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)


In [2]:
CWD = "/".join(os.getcwd().split("/")[:-2])
lcs = pd.read_csv(f"{CWD}/data/summary/lcs.csv")
lcs

ID  QCS  typ  cadence_min mission prefix   origin h_mission SpT  \
0  100004076   14  slc            1     kep    KIC  generic    Kepler  L1   
1  212035340   18  llc           30    ktwo   EPIC  generic        K2  M8   
2  237880881    1  slc            2    tess    TIC  generic      TESS  M5   
3   44984200   10  slc            2    tess    TIC   custom      TESS  M6   
4  277539431   12  slc            2    tess    TIC   custom      TESS  M7   
5  300741820    8  slc            2    tess    TIC  generic      TESS  M6   
6  230120143   16  slc            2    tess    TIC  generic      TESS  M7   

   view_start  ...       J      R   Gaia_G  vsini_kms  e_vsini_kms    Prot_d  \
0     1356.50  ...  13.078    NaN  17.8356       11.2          2.2  0.370150   
1     3437.00  ...  15.900    NaN  19.5667        NaN          NaN  0.193000   
2     1331.00  ...  11.530    NaN  14.9796       14.4          2.6  0.351250   
3     1587.25  ...  10.309  15.08  14.4115        NaN          NaN  0.113000   
4     1641.00  ...  10.630    NaN  14.7381        NaN          NaN  0.190000   
5     1522.00  ...  11.959    NaN  15.3277        NaN          NaN  0.132000   
6     1741.00  ...   9.854    NaN  13.5570       10.8          0.7  0.378325   

        sini           Ref                 identifier  Rstar  
0       >.59      Gizis+13  WISEP J190648.47+401106.8  0.107  
1        NaN     Paudel+19    MASS J08371832+2050349   0.111  
2        NaN      Kraus+14    2MASS J01180670-6258591  0.199  
3        NaN     this work             SCR J0838-5855    NaN  
4        NaN     this work  WISEA J105515.71-735611.3    NaN  
5        NaN       Zhan+19           UCAC4 116-015389    NaN  
6  0.6844128  Kesseli+2018                        NaN    NaN  

[7 rows x 32 columns]

In [3]:
lcs= lcs.loc[:5,]
lcs


ID  QCS  typ  cadence_min mission prefix   origin h_mission SpT  \
0  100004076   14  slc            1     kep    KIC  generic    Kepler  L1   
1  212035340   18  llc           30    ktwo   EPIC  generic        K2  M8   
2  237880881    1  slc            2    tess    TIC  generic      TESS  M5   
3   44984200   10  slc            2    tess    TIC   custom      TESS  M6   
4  277539431   12  slc            2    tess    TIC   custom      TESS  M7   
5  300741820    8  slc            2    tess    TIC  generic      TESS  M6   

   view_start  ...       J      R   Gaia_G  vsini_kms  e_vsini_kms   Prot_d  \
0     1356.50  ...  13.078    NaN  17.8356       11.2          2.2  0.37015   
1     3437.00  ...  15.900    NaN  19.5667        NaN          NaN  0.19300   
2     1331.00  ...  11.530    NaN  14.9796       14.4          2.6  0.35125   
3     1587.25  ...  10.309  15.08  14.4115        NaN          NaN  0.11300   
4     1641.00  ...  10.630    NaN  14.7381        NaN          NaN  0.19000   
5     1522.00  ...  11.959    NaN  15.3277        NaN          NaN  0.13200   

   sini        Ref                 identifier  Rstar  
0  >.59   Gizis+13  WISEP J190648.47+401106.8  0.107  
1   NaN  Paudel+19    MASS J08371832+2050349   0.111  
2   NaN   Kraus+14    2MASS J01180670-6258591  0.199  
3   NaN  this work             SCR J0838-5855    NaN  
4   NaN  this work  WISEA J105515.71-735611.3    NaN  
5   NaN    Zhan+19           UCAC4 116-015389    NaN  

[6 rows x 32 columns]

In [4]:
def get_period_get_amplitude(target, plot=False, save=False, plotmini=False):
    """Fit a sinusoidal modulation and
    subtract it from the flux.

    Parameters:
    -----------
    target : Series
        Description of the target.
    plot : bool
        If True, will plot the periodogram
    save : bool
        If True, will save periodogram plot to file.

    Return:
    -------
    time, subtracted flux, model, period:
    array, array, array, astropy.Quantity
    """
    def cosine(x, a, b, c, d, e):
        """cosine with a linear trend"""
        return a * np.cos(b * x + c) + d * x + e

    # Fetch light curve
#     if target.origin=="custom":
    flck = fetch_lightcurve(target, flux_type="PDCSAP_FLUX")
#     else: 
#         flck = flc

    # Get the dominant modulation period
    period, mfp = find_period(target, save=False, plot=False, custom=target.origin, flc=flck)

    # Optimize for the model parameters using
    # non-linear least-squares (Levenberg-Marquardt):
    cond = np.invert(np.isnan(flck.time)) & np.invert(np.isnan(flck.flux))
#     if cut is not None:
#         cond = cond & (flck.time > cut[0]) & (flck.time < cut[1])
    p, p_cov = optimize.curve_fit(cosine, flck.time[cond],
                                  flck.flux[cond],
                                  p0=[np.nanstd(flck.flux), 2 * np.pi * mfp.value,
                                      0, 0, np.nanmean(flck.flux)],
                                  method="lm")
    model = cosine(flck.time, p[0], p[1], p[2], p[3], p[4])
    subtracted_flux = np.nanmedian(flck.flux) + flck.flux - model
    print(target.ID, p)
    # Calculate the relative amplitude of the oscillation
    rel_amplitude = p[0] / np.nanmedian(flck.flux)
    return period, rel_amplitude, p

In [5]:
campaigns = {237880881:[1,2],
             44984200: [8,9,10],
             277539431:[12],
             300741820:[1,2,4,5,6,7,8,9,10,11,12,13],
            }
res = pd.DataFrame(columns=["ID","QCS","rel_amplitude","period_h"])
for label, row in lcs.iterrows():
    if row.ID in campaigns.keys():
        for C in campaigns[row.ID]: 
            row.QCS = C
            print(row.QCS)
            period, relampl, p = get_period_get_amplitude(row)
            res = res.append(dict(zip(["ID","QCS","rel_amplitude","period_h","phase_offset","lin_trend","offset_y"],
                                       [row.ID, C, abs(relampl),period.value, p[2],p[3],p[4]])),ignore_index=True)

10% (1972/20076) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
10% (1972/20076) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
7% (1420/19737) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
7% (1420/19737) of the cadences will be ignored due to the quality mask (quality_bitmask=175).


1
TIC 237880881 modulation period:  8.440140530163145 h
237880881 [-7.75192301e+00  1.78681079e+01 -1.55852265e+00  2.18150339e-02
  5.89294737e+02]
2
TIC 237880881 modulation period:  8.43155092474404 h
237880881 [-7.97574774e+00  1.78659283e+01  2.64977695e+01 -4.05869950e-03
  6.41593751e+02]
8
TIC 44984200 modulation period:  2.7113494815444104 h
44984200 [-6.37099832e+00  5.56126046e+01  6.43649000e+00 -5.24975756e+00
  9.22181443e+03]
9
TIC 44984200 modulation period:  2.7113734643352134 h
44984200 [-2.17111439e+00  5.56214524e+01 -7.29387452e+00 -1.49758472e+00
  2.77519632e+03]
10
TIC 44984200 modulation period:  2.7114843822240977 h
44984200 [ 8.25507467e+00  5.56007172e+01  2.17583380e+01 -2.49899814e+00
  5.64338931e+03]
12
TIC 277539431 modulation period:  4.556764823311947 h
277539431 [ 4.23320311e+00  3.30752837e+01  2.85623918e+01 -1.05034039e-01
  9.52266702e+02]

10% (1972/20076) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
10% (1972/20076) of the cadences will be ignored due to the quality mask (quality_bitmask=175).



1
TIC 300741820 modulation period:  3.1669978996888606 h


7% (1420/19737) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
7% (1420/19737) of the cadences will be ignored due to the quality mask (quality_bitmask=175).


...

TIC 300741820 modulation period:  3.168882194542465 h
300741820 [-3.05632410e+00  4.75908917e+01 -5.87482884e+00 -1.05162632e-03
  4.20126392e+02]
11
TIC 300741820 modulation period:  3.169329826933344 h


5% (1015/20119) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
5% (1015/20119) of the cadences will be ignored due to the quality mask (quality_bitmask=175).


300741820 [-2.86763781e+00  4.75939108e+01 -2.32402085e+01  6.80403419e-03
  4.03793101e+02]
12
TIC 300741820 modulation period:  3.1690633176693517 h
300741820 [-2.91134522e+00  4.75979679e+01 -2.36117827e+01  1.96108809e-03
  4.10901054e+02]
13


4% (896/20479) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
4% (896/20479) of the cadences will be ignored due to the quality mask (quality_bitmask=175).


TIC 300741820 modulation period:  3.167791089691277 h
300741820 [-2.82131149e+00  4.75914133e+01  1.86263885e+01 -1.32581560e-03
  4.15129600e+02]


In [6]:
res

ID   QCS  rel_amplitude  period_h  lin_trend     offset_y  \
0   237880881.0   1.0       0.012565  8.440141   0.021815   589.294737   
1   237880881.0   2.0       0.012542  8.431551  -0.004059   641.593751   
2    44984200.0   8.0       0.005242  2.711349  -5.249758  9221.814428   
3    44984200.0   9.0       0.004885  2.711373  -1.497585  2775.196324   
4    44984200.0  10.0       0.004895  2.711484  -2.498998  5643.389307   
5   277539431.0  12.0       0.005433  4.556765  -0.105034   952.266702   
6   300741820.0   1.0       0.006799  3.166998  -0.000037   395.270926   
7   300741820.0   2.0       0.006925  3.168026  -0.002845   408.525334   
8   300741820.0   4.0       0.007822  3.167797   0.047839   335.064205   
9   300741820.0   5.0       0.007803  3.169868   0.009517   418.947498   
10  300741820.0   6.0       0.008212  3.167448  -0.000505   415.825297   
11  300741820.0   7.0       0.008225  3.168125  -0.005500   439.778627   
12  300741820.0   8.0       0.007233  3.168673  -0.127683   601.750187   
13  300741820.0   9.0       0.007727  3.169821  -0.001605   415.063410   
14  300741820.0  10.0       0.007305  3.168882  -0.001052   420.126392   
15  300741820.0  11.0       0.006914  3.169330   0.006804   403.793101   
16  300741820.0  12.0       0.007031  3.169063   0.001961   410.901054   
17  300741820.0  13.0       0.006833  3.167791  -0.001326   415.129600   

    phase_offset  
0      -1.558523  
1      26.497769  
2       6.436490  
3      -7.293875  
4      21.758338  
5      28.562392  
6      24.473377  
7       9.375213  
8      12.828956  
9     -33.030710  
10     29.805058  
11     11.076377  
12     -4.705182  
13    -31.871512  
14     -5.874829  
15    -23.240208  
16    -23.611783  
17     18.626389

In [7]:
for i, g in res.groupby("ID"):
    print(i, g.rel_amplitude.mean(), g.rel_amplitude.std()/g.rel_amplitude.mean()*100)
    print(i, g.period_h.mean(), g.period_h.std()/g.period_h.mean()*100)

44984200.0 0.005007210887912111 4.055060354344716
44984200.0 2.7114024427012406 0.0026542630811061574
237880881.0 0.012553271108074231 0.13239634700357442
237880881.0 8.435845727453593 0.07199951772232983
277539431.0 0.005432627355323591 nan
277539431.0 4.556764823311947 nan
300741820.0 0.007402363204472216 7.176397896177508
300741820.0 3.1684851564244703 0.029359417206237873


## Fit period with MCMC


In [8]:
def cosine(x, a, b, c, d, e):
    """cosine with a linear trend"""
    return a * np.cos(b * x + c) + d * x + e


def logit(function):
    '''Make a probability distribution
    a log probability distribution.'''
    def wrapper(*args, **kwargs):
        result = function(*args, **kwargs)
        np.seterr(divide='ignore') # ignore division by zero because you want to have the -np.inf results
        result = np.log(result)
        return result
    return wrapper


@logit
def uninformative_prior(rate, minrate, maxrate):
    '''Uninformative prior for the rates.
    Uniform within [minrate, maxrate].

    Parameters:
    -------------
    rate : float

    minrate, maxrate : float
        interval in which rate is constrained

    Return:
        Prior probability
    '''
    condition = ~(np.isfinite(maxrate) & np.isfinite(minrate))
    if ((maxrate < minrate) | condition):
        raise ValueError("maxrate must be > minrate, and a finite value")
    if ((rate >= minrate) & (rate <= maxrate)):
        return 1. / (maxrate - minrate)
    else:
        return 0



def calculate_posterior_value_that_can_be_passed_to_mcmc(lp):
    '''Do some checks to make sure MCMC will work.'''
    if not np.isfinite(lp):
        return -np.inf
    if np.isnan(lp):
        return -np.inf
    else:
        return lp


def log_prior(p,):
    """Uniform prior

    """
    

    prior = (uninformative_prior(p[0], 0.1, .2) +
             uninformative_prior(p[1], 0, 1e6) +
             uninformative_prior(p[2],  0, 1e6) +
             uninformative_prior(p[3], -1e6, 1e6)  +
             uninformative_prior(p[4], 0, 1e8) )

    return calculate_posterior_value_that_can_be_passed_to_mcmc(prior)




def log_likelihood(p, time, flux, flux_err):
    """Log likelihood function assuming
    Gaussian uncertainties in the data points.
    SHOULDNT THIS BE POISSON? No, because flux_err is not exactly sqrt(n), 
    and above several hundred counts
    """


    
    model = cosine(time, p[1], 2*np.pi/p[0], p[2],p[3],p[4])

    fr2 = flux_err**2
    val = -0.5 * np.sum((flux - model) ** 2 / fr2 + np.log(fr2))

        
    return val


def log_probability(p, time, flux, flux_err):
    """Posterior probability to pass to MCMC sampler.
    """
    lp = log_prior(p)

    if not np.isfinite(lp):
        print("INF")
        return -np.inf
    
    try:
        ll = log_likelihood(p, time, flux, flux_err)
        
    except:
        print("FAIL")
        return -np.inf
    
    if np.isnan(ll):
        print("NAN")
        return -np.inf
    
    return lp + ll

In [9]:
ID = 237880881

qcs = res.loc[res.ID == ID, "QCS"].values

target = lcs[lcs.ID ==ID].iloc[0]
target

ID                           237880881
QCS                                  1
typ                                slc
cadence_min                          2
mission                           tess
prefix                             TIC
origin                         generic
h_mission                         TESS
SpT                                 M5
view_start                        1331
view_stop                       1333.5
view_min                           560
view_max                           700
BJDoff                         2457000
tstart                          1331.7
ampl_min                           NaN
ampl_max                           NaN
GRP                                NaN
plxmas                             NaN
eplxmas                            NaN
RA                              19.528
Dec                           -62.9831
J                                11.53
R                                  NaN
Gaia_G                         14.9796
vsini_kms                

In [10]:
for i in range(10):
    for QCS in qcs:
        # Pick sector
        target.QCS = int(QCS)
        print(target.QCS)
        print(f"{target.QCS:02d}")
        
        # Get light curve
        flcd = fetch_lightcurve(target, flux_type="PDCSAP_FLUX")

        # define flux, time and error arrays
        flcd.flux[((flcd.time > target.view_start) & (flcd.time < target.view_stop))] = np.nan
        flcd = flcd[np.where(np.isfinite(flcd.flux))]
        flcd = flcd.flatten(window_length=1001)
        time = flcd.time
        flux = flcd.flux
        flux_err = flcd.flux_err


        pick = (res.ID == ID) & (res.QCS==QCS)
        row = res.loc[pick, :].iloc[0]
        meanflux = np.nanmedian(flux)

        inits = [row.period_h/24., row.rel_amplitude * meanflux, row.phase_offset,  row.lin_trend, row.offset_y]
        print(inits)
        pos = inits * (1. + 1e-4 * np.random.randn(32, len(inits)))

        # Set up the backend
        # Don't forget to clear it in case the file already exists
        filename = f"{CWD}/analysis/results/mcmc/rotation/{tstamp}_{target.ID}_S{QCS:.0f}_MCMC.h5"
        backend = emcee.backends.HDFBackend(filename)
        #backend.reset(32, len(inits))
        args = (time, flux, flux_err)

        sampler = emcee.EnsembleSampler(32, len(inits), log_probability,
                                        args=args,backend=backend)


        start = Timestamp.time()
        sampler.run_mcmc(None, 500, progress=True, store=True)
        end = Timestamp.time()
        multi_data_time = end - start
        print("MCMC took {0:.1f} seconds".format(multi_data_time))

    #     tau = sampler.get_autocorr_time()
    #     burnin = int(2 * np.max(tau))
    #     thin = int(0.5 * np.min(tau))

        samples = sampler.get_chain(flat=True)
       # fig = corner.corner(samples)

        columns = ["Prot_d", "rel_amplitude","phase_offset","lin_trend","offset_y"]

        resultframe = pd.DataFrame(data=samples,
                               columns=columns)

        af = resultframe.quantile([.16,0.5,.84], axis=0)

        series = (pd.Series(af.loc[.16,]).
         rename(lambda x: x+"_16").
         append(pd.Series(af.loc[.5,]).
                rename(lambda x: x+"_50")).
         append(pd.Series(af.loc[.84,]).
                rename(lambda x: x+"_84")).
         append(pd.Series({"tstamp":tstamp,
                           "ID":target.ID,
                           "QCS":QCS,
                           "prefix":target.prefix,
                           "Prot_d_LS":row.period_h/24.,
                           "rel_amplitude_init":row.rel_amplitude, 
                           "phase_offset_init":row.phase_offset,
                           "lin_trend_init":row.lin_trend, 
                           "offset_y":row.offset_y,
                           "steps":resultframe.shape[0]//32
                           })).
         sort_index(ascending=True))
        with open(f"{CWD}/analysis/results/mcmc/rotation/mcmc_rotation_output.csv","a") as f:
            #Add more lines here
            pd.DataFrame(series).T.to_csv(f, index=False, header=False)
            
    Timestamp.sleep(10)

10% (1972/20076) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
10% (1972/20076) of the cadences will be ignored due to the quality mask (quality_bitmask=175).
  0%|          | 0/500 [00:00<?, ?it/s]

1
01
[0.35167252209013106, 0.012565023273955497, -1.558522648226842, 0.021815033898334436, 589.2947374291932]
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF

  3%|▎         | 13/500 [00:00<00:03, 129.74it/s]


INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF

  5%|▌         | 26/500 [00:00<00:03, 129.36it/s]

...

INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF


 97%|█████████▋| 485/500 [00:03<00:00, 128.73it/s]

INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF


100%|██████████| 500/500 [00:03<00:00, 128.50it/s]


INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF
INF


In [11]:
df = pd.read_csv(f"{CWD}/analysis/results/mcmc/rotation/mcmc_rotation_output.csv")
df = df[(df.ID==ID) & (df.tstamp == tstamp) ]
#print(df)

for s, g in df.groupby("QCS"):
    plt.figure()
    g['uperr'] = g.Prot_d_84-g.Prot_d_50
    g['loerr'] = g.Prot_d_50-g.Prot_d_16
    plt.scatter(x=g.steps, y=g.Prot_d_50)#, yerr=g[["loerr","uperr"]].values.T)
plt.plot(g.steps, g.Prot_d_LS, c="r")
plt.title(s)
plt.ylim(target.Prot_d*.995,target.Prot_d*2.005,)

NumExpr defaulting to 8 threads.


(0.34949375, 0.70425625)

In [12]:
df2 = df[df.steps>10000]
plt.scatter(df2.QCS, df2.Prot_d_50)

In [13]:
# truths=[phi_a, theta_a, a, fwhm,i_mu, phi0]);
plt.hist(samples.T[0], bins=np.linspace(0,.2, 300));

In [14]:
model = cosine(time, result[1][1], 2.*np.pi/result[0][1], result[2][1],result[3][1],result[4][1])
# model = cosine(time, inits[1]*.5, 2.*np.pi/inits[0], 2.*np.pi/8.5, 0., inits[4])

NameError: name 'result' is not defined

In [ ]:

target.QCS = 4
print(target.QCS)
print(f"{target.QCS:02d}")

# Get light curve
flcd = fetch_lightcurve(target, flux_type="PDCSAP_FLUX")

# define flux, time and error arrays
flcd.flux[((flcd.time > target.view_start) & (flcd.time < target.view_stop))] = np.nan
flcd = flcd[np.where(np.isfinite(flcd.flux))]
flcd = flcd.flatten(window_length=1001)
time = flcd.time
flux = flcd.flux
flux_err = flcd.flux_err
plt.figure(figsize=(16,3))
plt.plot(time, flux);
#plt.plot(time, model)
# plt.xlim(1592,1594)
#plt.xlim(1429,1430)

In [ ]:
target.QCS = 4
print(target.QCS)
print(f"{target.QCS:02d}")

# Get light curve
flcd = fetch_lightcurve(target, flux_type="PDCSAP_FLUX")

# define flux, time and error arrays
flcd.flux[((flcd.time > target.view_start) & (flcd.time < target.view_stop))] = np.nan
flcd = flcd[np.where(np.isfinite(flcd.flux))]
flcd = flcd.flatten(window_length=1001)
time = flcd.time
flux = flcd.flux
flux_err = flcd.flux_err
plt.figure(figsize=(15,4))
plt.plot(time, flux)
#plt.plot(time, model)
# plt.xlim(1592,1594)
plt.xlim(1415,1418)

In [ ]:
for QCS in [1,4,7]:
    period, mfp = find_period(target, save=False, minfreq=2, maxfreq=24, custom=True)

In [ ]:
for QCS in [2,5,6,8,9,10,11,12,13]:
    period, mfp = find_period(target, save=False, minfreq=2, maxfreq=24, custom=True)

In [ ]:
5.8/7.5

In [ ]:
3.17/24

In [ ]:
0.17182598100709*24